In [1]:
from huggingface_hub import notebook_login

notebook_login()

In [2]:
from datasets import load_dataset, DatasetDict

vivos = DatasetDict()

vivos["train"] = load_dataset("vivos", split="train", use_auth_token=True)
vivos["test"] = load_dataset("vivos", split="test", use_auth_token=True)




Found cached dataset vivos (/home/tesla/.cache/huggingface/datasets/vivos/default/1.1.0/ab59078eb266c1a0ea856786ba56b5b8d56f29b42dfb37d92115cf81a7b1a5e0)
Found cached dataset vivos (/home/tesla/.cache/huggingface/datasets/vivos/default/1.1.0/ab59078eb266c1a0ea856786ba56b5b8d56f29b42dfb37d92115cf81a7b1a5e0)


In [38]:
vivos

DatasetDict({
    train: Dataset({
        features: ['speaker_id', 'path', 'audio', 'sentence'],
        num_rows: 11660
    })
    test: Dataset({
        features: ['speaker_id', 'path', 'audio', 'sentence'],
        num_rows: 760
    })
})

In [3]:
vivos_clean = vivos.remove_columns(["speaker_id", "path"])

In [40]:
vivos_clean

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 11660
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 760
    })
})

In [79]:
print(vivos_clean['train'][12])

{'audio': {'path': 'vivos/train/waves/VIVOSSPK27/VIVOSSPK27_084.wav', 'array': array([ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
        9.15527344e-05, -5.18798828e-04, -9.15527344e-04]), 'sampling_rate': 16000}, 'sentence': 'CHƯA HẾT ĐI KHIẾU NẠI THÌ NHÀ MẠNG BẢO VỀ ĐẠI LÝ CHỌN SỐ KHÁC ĐI'}


In [4]:

common_voice = DatasetDict()

common_voice["train"] = load_dataset("mozilla-foundation/common_voice_13_0", "vi", split="train+validation", use_auth_token=True)
common_voice["test"] = load_dataset("mozilla-foundation/common_voice_13_0", "vi", split="test", use_auth_token=True)




Found cached dataset common_voice_13_0 (/home/tesla/.cache/huggingface/datasets/mozilla-foundation___common_voice_13_0/vi/13.0.0/2506e9a8950f5807ceae08c2920e814222909fd7f477b74f5d225802e9f04055)
Found cached dataset common_voice_13_0 (/home/tesla/.cache/huggingface/datasets/mozilla-foundation___common_voice_13_0/vi/13.0.0/2506e9a8950f5807ceae08c2920e814222909fd7f477b74f5d225802e9f04055)


In [42]:
common_voice

DatasetDict({
    train: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'variant'],
        num_rows: 2854
    })
    test: Dataset({
        features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'variant'],
        num_rows: 1225
    })
})

In [67]:
common_voice_clean = common_voice.remove_columns(["client_id", "path", "down_votes", "gender", "locale", "segment", "up_votes", "age", "accent", "variant"])


In [89]:
common_voice_clean

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 2854
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 1225
    })
})

In [1]:
from datasets import DatasetDict

def convert_to_uppercase(example):
    example["sentence"] = example["sentence"].upper()
    return example

common_voice_clear = DatasetDict()

common_voice_clear["train"] = common_voice_clean["train"].map(convert_to_uppercase)
common_voice_clear["test"] = common_voice_clean["test"].map(convert_to_uppercase)

NameError: name 'common_voice_clean' is not defined

In [93]:
print(common_voice_clear['train'][1])

{'audio': {'path': '/home/tesla/.cache/huggingface/datasets/downloads/extracted/acb70896120347904e003bb826dcabc1ddd05a02210935cb44ce1c807e8742a5/vi_train_0/common_voice_vi_23901118.mp3', 'array': array([ 0.00000000e+00,  4.20543185e-14,  1.38823347e-14, ...,
       -8.41874498e-06, -8.36193431e-06, -6.76584477e-06]), 'sampling_rate': 48000}, 'sentence': 'KHI CON CÓ MẸ'}


In [94]:
from pydub import AudioSegment
import os

from tqdm import tqdm

def convert_mp3_to_wav(mp3_path, wav_path, target_sampling_rate):
    audio = AudioSegment.from_mp3(mp3_path)
    audio = audio.set_frame_rate(target_sampling_rate)
    audio.export(wav_path, format='wav')

target_sampling_rate = 16000

for example in tqdm(common_voice_clear["train"]):
    mp3_path = example["audio"]["path"]
    wav_path = os.path.splitext(mp3_path)[0] + ".wav"
    convert_mp3_to_wav(mp3_path, wav_path, target_sampling_rate)
    example["audio"]["path"] = wav_path



100%|██████████| 2854/2854 [33:25<00:00,  1.42it/s]


In [95]:
import datasets
from datasets import Audio

common_voice_clean = common_voice_clean.cast_column("audio", Audio(sampling_rate=16000))

In [47]:
concat = DatasetDict()

In [96]:
concat["train"] = datasets.concatenate_datasets([common_voice_clean["train"], vivos_clean["train"]])

#concat['test']= datasets.concatenate_datasets([common_voice_clean["test"], vivos_clean["test"]])
concat['test']= vivos_clean["test"]


In [97]:
concat

DatasetDict({
    train: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 14514
    })
    test: Dataset({
        features: ['audio', 'sentence'],
        num_rows: 760
    })
})

In [98]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")


In [99]:
from transformers import WhisperTokenizerFast

tokenizer = WhisperTokenizerFast.from_pretrained("openai/whisper-small", language="Vietnamese", task="transcribe")


In [80]:
input_str = concat["train"][8550]["sentence"]
labels = tokenizer(input_str).input_ids
decoded_with_special = tokenizer.decode(labels, skip_special_tokens=False)
decoded_str = tokenizer.decode(labels, skip_special_tokens=True)

print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")


Input:                 KHÔNG CÓ AI BÁC BỎ QUYỀN ĐÓ
Decoded w/ special:    <|startoftranscript|><|notimestamps|>KHÔNG CÓ AI BÁC BỎ QUYỀN ĐÓ<|endoftext|>
Decoded w/out special: KHÔNG CÓ AI BÁC BỎ QUYỀN ĐÓ
Are equal:             True


In [100]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Vietnamese", task="transcribe")


In [19]:
from datasets import Audio

concat = concat.cast_column("audio", Audio(sampling_rate=16000))

In [59]:
print(concat["train"][4500])

{'audio': {'path': 'vivos/train/waves/VIVOSSPK12/VIVOSSPK12_R077.wav', 'array': array([ 0.00000000e+00,  0.00000000e+00, -3.05175781e-05, ...,
        1.31225586e-03,  1.12915039e-03,  1.55639648e-03]), 'sampling_rate': 16000}, 'sentence': 'KIÊN GIANG'}


In [101]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids 
    batch["labels"] = tokenizer(batch["sentence"]).input_ids
    return batch


In [102]:
concat = concat.map(prepare_dataset, remove_columns=concat.column_names["train"], num_proc=6)

Map (num_proc=6):   0%|          | 0/14514 [00:00<?, ? examples/s]

Map (num_proc=6):   0%|          | 0/760 [00:00<?, ? examples/s]

In [103]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [104]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [105]:
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"  

Train


In [106]:
import evaluate

metric = evaluate.load("wer")


def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [107]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")


In [108]:
model.config.forced_decoder_ids = None
model.config.suppress_tokens = []

In [109]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./vi_whisper-small",  # change to a repo name of your choice
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-4,
    warmup_steps=1000,
    max_steps=8000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=4000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
)


In [126]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=concat["train"],

    eval_dataset=concat["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)


/media/tesla/New Volume1/DEMO/DUY/Vietnamese_ASR/./vi_whisper-small is already a clone of https://huggingface.co/DuyTa/vi_whisper-small. Make sure you pull the latest changes with `repo.git_pull()`.


OSError: From https://huggingface.co/DuyTa/vi_whisper-small
   d7893fc..47c00b5  main       -> origin/main
hint: You have divergent branches and need to specify how to reconcile them.
hint: You can do so by running one of the following commands sometime before
hint: your next pull:
hint: 
hint:   git config pull.rebase false  # merge (the default strategy)
hint:   git config pull.rebase true   # rebase
hint:   git config pull.ff only       # fast-forward only
hint: 
hint: You can replace "git config" with "git config --global" to set a default
hint: preference for all repositories. You can also pass --rebase, --no-rebase,
hint: or --ff-only on the command line to override the configured default per
hint: invocation.
fatal: Need to specify how to reconcile divergent branches.


In [130]:
tokenizer.save_pretrained("./vi_whisper-small/")

('./vi_whisper-small/tokenizer_config.json',
 './vi_whisper-small/special_tokens_map.json',
 './vi_whisper-small/vocab.json',
 './vi_whisper-small/merges.txt',
 './vi_whisper-small/normalizer.json',
 './vi_whisper-small/added_tokens.json',
 './vi_whisper-small/tokenizer.json')

In [31]:
import torch

device_count = torch.cuda.device_count()

for device in range(device_count):
    torch.cuda.device(device)
    allocated_memory = torch.cuda.memory_allocated(device)
    peak_memory = torch.cuda.max_memory_allocated(device)
    print(f"Device {device}:")
    print(f"  Currently allocated memory: {allocated_memory / 1024**2} MB")
    print(f"  Peak memory usage: {peak_memory / 1024**2} MB")



Device 0:
  Currently allocated memory: 922.884765625 MB
  Peak memory usage: 922.884765625 MB


In [32]:
device_count = torch.cuda.device_count()

for device in range(device_count):
    properties = torch.cuda.get_device_properties(device)
    print(f"Device {device}:")
    print(f"  Name: {properties.name}")
    print(f"  Max Memory: {properties.total_memory / 1024**2} MB")


Device 0:
  Name: Tesla T4
  Max Memory: 14966.375 MB


In [111]:
trainer.train()

/home/tesla/miniconda3/envs/DUY/lib/python3.9/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


  0%|          | 0/8000 [00:00<?, ?it/s]

{'loss': 3.8537, 'learning_rate': 2.1000000000000002e-06, 'epoch': 0.03}
{'loss': 2.2347, 'learning_rate': 4.6e-06, 'epoch': 0.06}
{'loss': 1.2627, 'learning_rate': 7.1e-06, 'epoch': 0.08}
{'loss': 0.8976, 'learning_rate': 9.600000000000001e-06, 'epoch': 0.11}
{'loss': 0.7313, 'learning_rate': 1.2100000000000001e-05, 'epoch': 0.14}
{'loss': 0.6526, 'learning_rate': 1.4599999999999999e-05, 'epoch': 0.17}
{'loss': 0.7221, 'learning_rate': 1.7000000000000003e-05, 'epoch': 0.19}
{'loss': 0.6478, 'learning_rate': 1.9500000000000003e-05, 'epoch': 0.22}
{'loss': 1.7029, 'learning_rate': 2.19e-05, 'epoch': 0.25}
{'loss': 1.1476, 'learning_rate': 2.44e-05, 'epoch': 0.28}
{'loss': 0.5837, 'learning_rate': 2.6900000000000003e-05, 'epoch': 0.3}
{'loss': 0.5912, 'learning_rate': 2.94e-05, 'epoch': 0.33}
{'loss': 0.6872, 'learning_rate': 3.19e-05, 'epoch': 0.36}
{'loss': 0.4103, 'learning_rate': 3.4399999999999996e-05, 'epoch': 0.39}
{'loss': 0.4293, 'learning_rate': 3.69e-05, 'epoch': 0.41}
{'loss'

  0%|          | 0/95 [00:00<?, ?it/s]

{'eval_loss': 0.3765707015991211, 'eval_wer': 32.16783216783217, 'eval_runtime': 349.1035, 'eval_samples_per_second': 2.177, 'eval_steps_per_second': 0.272, 'epoch': 1.1}
{'loss': 0.2729, 'learning_rate': 9.972857142857144e-05, 'epoch': 1.13}
{'loss': 0.267, 'learning_rate': 9.937142857142857e-05, 'epoch': 1.16}
{'loss': 0.2617, 'learning_rate': 9.901428571428571e-05, 'epoch': 1.18}
{'loss': 0.2613, 'learning_rate': 9.865714285714286e-05, 'epoch': 1.21}
{'loss': 0.2736, 'learning_rate': 9.83e-05, 'epoch': 1.24}
{'loss': 0.245, 'learning_rate': 9.794285714285714e-05, 'epoch': 1.27}
{'loss': 0.2385, 'learning_rate': 9.75857142857143e-05, 'epoch': 1.29}
{'loss': 0.258, 'learning_rate': 9.722857142857144e-05, 'epoch': 1.32}
{'loss': 0.2623, 'learning_rate': 9.687142857142858e-05, 'epoch': 1.35}
{'loss': 0.2346, 'learning_rate': 9.651428571428572e-05, 'epoch': 1.38}
{'loss': 0.2376, 'learning_rate': 9.615714285714286e-05, 'epoch': 1.4}
{'loss': 0.246, 'learning_rate': 9.58e-05, 'epoch': 1.4

...

  0%|          | 0/95 [00:00<?, ?it/s]

{'eval_loss': 0.3143082559108734, 'eval_wer': 27.169127169127172, 'eval_runtime': 357.6908, 'eval_samples_per_second': 2.125, 'eval_steps_per_second': 0.266, 'epoch': 7.71}
{'loss': 0.0032, 'learning_rate': 1.402857142857143e-05, 'epoch': 7.74}
{'loss': 0.0028, 'learning_rate': 1.3671428571428571e-05, 'epoch': 7.76}
{'loss': 0.0033, 'learning_rate': 1.3314285714285715e-05, 'epoch': 7.79}
{'loss': 0.0052, 'learning_rate': 1.2957142857142856e-05, 'epoch': 7.82}
{'loss': 0.0023, 'learning_rate': 1.2600000000000001e-05, 'epoch': 7.85}
{'loss': 0.0034, 'learning_rate': 1.2242857142857143e-05, 'epoch': 7.87}
{'loss': 0.0026, 'learning_rate': 1.1885714285714286e-05, 'epoch': 7.9}
{'loss': 0.0022, 'learning_rate': 1.1528571428571428e-05, 'epoch': 7.93}
{'loss': 0.0037, 'learning_rate': 1.1171428571428571e-05, 'epoch': 7.96}
{'loss': 0.003, 'learning_rate': 1.0814285714285715e-05, 'epoch': 7.98}
{'loss': 0.0009, 'learning_rate': 1.0457142857142856e-05, 'epoch': 8.01}
{'loss': 0.0006, 'learning_

  0%|          | 0/95 [00:00<?, ?it/s]

{'eval_loss': 0.318661630153656, 'eval_wer': 27.36337736337736, 'eval_runtime': 356.3989, 'eval_samples_per_second': 2.132, 'eval_steps_per_second': 0.267, 'epoch': 8.81}
{'train_runtime': 48216.7702, 'train_samples_per_second': 2.655, 'train_steps_per_second': 0.166, 'train_loss': 0.13303363310021815, 'epoch': 8.81}


TrainOutput(global_step=8000, training_loss=0.13303363310021815, metrics={'train_runtime': 48216.7702, 'train_samples_per_second': 2.655, 'train_steps_per_second': 0.166, 'train_loss': 0.13303363310021815, 'epoch': 8.81})

In [34]:
pt_model = WhisperForConditionalGeneration.from_pretrained("./whisper-base-vi/pytorch_model.bin", from_tf=True)
pt_model.save_pretrained("./whisper-base-vi/vi_whisper.pt")

OSError: It looks like the config file at './whisper-base-vi/pytorch_model.bin' is not a valid JSON file.

In [ ]:
kwargs = {
    "dataset_tags": "vivos-commonvoice",
    "dataset": "Vivos",  
    "language": "vi",
    "model_name": "Whisper Small Vi - Duy Ta", 
    "finetuned_from": "openai/whisper-small",
    "tasks": "automatic-speech-recognition",
    "config" : None
}


In [131]:
trainer.push_to_hub(commit_message="change")

Several commits (2) will be pushed upstream.
The progress bars may be unreliable.
error: The destination you provided is not a full refname (i.e.,
starting with "refs/"). We tried to guess what you meant by:

- Looking for a ref that matches 'HEAD' on the remote side.
- Checking if the <src> being pushed ('HEAD')
  is a ref in "refs/{heads,tags}/". If so we add a corresponding
  refs/{heads,tags}/ prefix on the remote side.

Neither worked, so we gave up. You must fully qualify the ref.
hint: The <src> part of the refspec is a commit object.
hint: Did you mean to create a new branch by pushing to
hint: 'HEAD:refs/heads/HEAD'?
error: failed to push some refs to 'https://huggingface.co/DuyTa/vi_whisper-small'



OSError: error: The destination you provided is not a full refname (i.e.,
starting with "refs/"). We tried to guess what you meant by:

- Looking for a ref that matches 'HEAD' on the remote side.
- Checking if the <src> being pushed ('HEAD')
  is a ref in "refs/{heads,tags}/". If so we add a corresponding
  refs/{heads,tags}/ prefix on the remote side.

Neither worked, so we gave up. You must fully qualify the ref.
hint: The <src> part of the refspec is a commit object.
hint: Did you mean to create a new branch by pushing to
hint: 'HEAD:refs/heads/HEAD'?
error: failed to push some refs to 'https://huggingface.co/DuyTa/vi_whisper-small'


In [ ]:
from transformers import WhisperForConditionalGeneration, WhisperProcessor

model = WhisperForConditionalGeneration.from_pretrained("DuyTa/vi_whisper")
processor = WhisperProcessor.from_pretrained("DuyTa/vi_whisper")


In [36]:
from transformers import pipeline
import gradio as gr

pipe = pipeline(model="./vi_whisper-small")  

def transcribe(audio):
    text = pipe(audio)["text"]
    return text

iface = gr.Interface(
    fn=transcribe,
    inputs=gr.Audio(source="upload", type="filepath"),
    outputs="text",
    title="Whisper Base Vietnamese",
    description="Realtime demo for Vietnamese speech recognition using a fine-tuned Whisper base model.",
)

iface.launch()

RuntimeError: Instantiating a pipeline without a task set raised an error: Repo id must use alphanumeric chars or '-', '_', '.', '--' and '..' are forbidden, '-' and '.' cannot start or end the name, max length is 96: './vi_whisper-small'.